In [46]:
#!/usr/bin/env python
from googleads import adwords

In [47]:
import time

In [48]:
from StringIO import StringIO
import pandas as pd
import numpy as np
import sys

In [248]:
class google_adwords(object):
    def __init__(self, country, start=20170601, end=20170801, max_ads=6, min_impressions=0, max_operations=3000,
                 verbose=False):
        self._country = country
        self._client = adwords.AdWordsClient.LoadFromStorage()
        self._page_size = 100
        self._max_ads = max_ads
        self._min_impressions = min_impressions
        self._start = start
        self._end = end
        self._active = 20170718
        self._version = 'v201609'
        self._max_operations = max_operations
        self._verbose = verbose
    
    def get_accounts(self, with_names=False):
        """Get all accounts excluding the hidden accounts"""
        managed_customer_service = self._client.GetService('ManagedCustomerService', version=self._version)
        selector = {
            'fields': ['AccountLabels','CustomerId',  'Name', 'CanManageClients', 'CurrencyCode'],
            'predicates': [{'field' : 'ExcludeHiddenAccounts',
                            'operator' : 'EQUALS' ,
                            'values' : 'true'
                            }]
        }    
        account_ids = []
        account_names = []
        page = managed_customer_service.get(selector)
        if 'entries' in page and page['entries']:
            for account in page['entries']:
                if str(account['name']).startswith(self._country + '_') and 'jobseeker' in str(account['name']) \
                    and '_aed_' not in str(account['name']) and '_app' not in str(account['name'])\
                    and '_display_' not in str(account['name']) and '_content_' not in str(account['name'])\
                    and '_dsa_' not in str(account['name']):              
                    account_ids.append(str(account['customerId'])) 
                    account_names.append(str(account['name'])) 
                    #for i in account: print i
        if with_names:
            return zip(account_ids, account_names)
        else:
            return account_ids
        
        
    def get_campaigns(self, account_id):
        self._client.SetClientCustomerId(account_id)
        campaign_service = self._client.GetService('CampaignService', version=self._version)
    
        enabled_campaigns = []
        offset = 0
        qry = ('SELECT Id, Name, Status '
               'DURING {start},{end} ORDER BY Name LIMIT {lower}, {upper}')
    
        more_pages = True
        while more_pages:
            page = campaign_service.query(qry.format(lower=offset, 
                                                     upper=self._page_size,
                                                     start=self._start,
                                                     end=self._end))
            if 'entries' in page:
                for campaign in page['entries']:
                    if campaign['status']=='ENABLED' and campaign['name'].lower().find("dynamic search ads")==-1:
                        enabled_campaigns.append(str(campaign['id']))
    
            offset += self._page_size
            more_pages = offset < int(page['totalNumEntries'])
            time.sleep(1)
        return enabled_campaigns
        
    def get_campaigns_via_report(self, account_id, with_names=False):
        #Using DownloadReportWithAwql just to test it
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        
        report_query = ('SELECT CampaignId, CampaignName, CampaignStatus, Clicks, Impressions '
               'FROM CAMPAIGN_PERFORMANCE_REPORT WHERE Impressions > 100 '
               'DURING {start},{end}'.format(start=self._start, end=self._end))
        _file = open('tmp.csv', 'w+')
        report_downloader.DownloadReportWithAwql(report_query, 'CSV', _file, skip_report_header=True,
                                                 skip_column_header=False, skip_report_summary=True,
                                                 include_zero_impressions=True)
        _file.close() 
        data = pd.read_csv('tmp.csv')
        data = data[~data['Campaign'].str.contains('tst')] # filter tst campaigns
        data = data[data['Campaign state']=='enabled'] # only enabled campaigns
        #data = data.sort_values('Impressions')
        if with_names:
            return zip(list(data['Campaign ID'].values), list(data['Campaign'].values))
        else:
            return list(data['Campaign ID'].values)
           
    def get_ad_groups_via_report(self, account_id, campaign_id):
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        qry = ('SELECT AdGroupId, Impressions, Clicks, Cost FROM '
                        'ADGROUP_PERFORMANCE_REPORT WHERE AdGroupStatus IN [ENABLED] '
                        'AND CampaignId={campaign_id} DURING {start},{end}'.format(start=self._start, 
                                                                                   end=self._end,
                                                                                   campaign_id=campaign_id))
        stream_data = report_downloader.DownloadReportAsStringWithAwql(qry, 'CSV',
                skip_report_header=True, skip_column_header=False,
                skip_report_summary=True, include_zero_impressions=True)
        report_data = StringIO(stream_data)
        report_df = pd.DataFrame.from_csv(report_data, sep=',').reset_index()
        return report_df

    def get_ad_data_via_report(self, account_id, campaign_id, ad_group_id):
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        qry = ('SELECT CampaignId, AdGroupId, Id, AdType, Impressions, Clicks, Cost FROM '
               'AD_PERFORMANCE_REPORT WHERE Status IN [ENABLED] AND CampaignId={2} AND '
               'AdGroupId={3} DURING {0}, {1}').format(self._start, self._end, campaign_id, ad_group_id)  
        stream_data = report_downloader.DownloadReportAsStringWithAwql(qry, 'CSV',
                skip_report_header=True, skip_column_header=False,
                skip_report_summary=True, include_zero_impressions=True)
        report_data = StringIO(stream_data)
        report_df = pd.DataFrame.from_csv(report_data, sep=',').reset_index()
        return report_df
    
    def get_not_eta_ad_data_via_report_backup(self, account_id, campaign_id):
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        qry = ('SELECT CampaignId, AdGroupId, AdGroupStatus, Id, AdType, Impressions, Clicks, Cost FROM '
               'AD_PERFORMANCE_REPORT WHERE Status IN [ENABLED] AND CampaignId={2} AND AdType=TEXT_AD '
               'AND AdGroupStatus in [ENABLED, PAUSED] DURING {0}, {1}').format(self._start, self._end, campaign_id)  
        stream_data = report_downloader.DownloadReportAsStringWithAwql(qry, 'CSV',
                skip_report_header=True, skip_column_header=False,
                skip_report_summary=True, include_zero_impressions=True)
        report_data = StringIO(stream_data)
        report_df = pd.DataFrame.from_csv(report_data, sep=',').reset_index()
        report_df = report_df.sort_values('Impressions', ascending=True)
        return report_df
    
    def get_not_eta_ad_data_via_report(self, account_id, campaign_id):
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        qry = ('SELECT CampaignId, AdGroupId, AdGroupStatus, Id, AdType, Impressions, Clicks, Cost FROM '
               'AD_PERFORMANCE_REPORT WHERE Status IN [ENABLED] AND CampaignId={2} '
               'AND AdGroupStatus in [ENABLED, PAUSED] DURING {0}, {1}').format(self._start, self._end, campaign_id)  
        stream_data = report_downloader.DownloadReportAsStringWithAwql(qry, 'CSV',
                skip_report_header=True, skip_column_header=False,
                skip_report_summary=True, include_zero_impressions=True)
        report_data = StringIO(stream_data)
        report_df = pd.DataFrame.from_csv(report_data, sep=',').reset_index()
        report_df = report_df.sort_values('Impressions', ascending=True)
        print 'non-eta %:', len(report_df[report_df['Ad type']=='Text ad'])*1.0/len(report_df)
        return report_df[report_df['Ad type']=='Text ad']
    
    def get_paused_ad_data_per_campaign_via_report(self, account_id, campaign_id):
        self._client.SetClientCustomerId(account_id)
        report_downloader = self._client.GetReportDownloader(version=self._version)
        qry = ('SELECT CampaignId, AdGroupId, Id, Status, Impressions, Clicks, Cost FROM '
               'AD_PERFORMANCE_REPORT WHERE Status IN [PAUSED] AND CampaignId={2} '
               'DURING {0}, {1}').format(self._start, self._end, campaign_id)  
        stream_data = report_downloader.DownloadReportAsStringWithAwql(qry, 'CSV',
                skip_report_header=True, skip_column_header=False,
                skip_report_summary=True, include_zero_impressions=True)
        report_data = StringIO(stream_data)
        report_df = pd.DataFrame.from_csv(report_data, sep=',').reset_index()
        return report_df


    def delete_ads(self, account_id, ad_group_id, ad_id):
        self._client.SetClientCustomerId(account_id)
        ad_group_ad_service = self._client.GetService('AdGroupAdService', version=self._version)
        
        #construct operations
        operations = []
        for i in ad_id:
            operations.append({'operator': 'REMOVE', 
                               'operand': {'xsi_type': 'AdGroupAd',
                                           'adGroupId': ad_group_id,
                                           'ad': {'id': i}
                                          }
                               })
        
        result = ad_group_ad_service.mutate(operations)

        # Display results.
        for ad in result['value']:
            print ('Ad with id "{0}" and type "{1}" was deleted.'.format(ad['ad']['id'], ad['ad']['Ad.Type']))
    
    def delete_multiple_ads(self, account_id, data):
        self._client.SetClientCustomerId(account_id)
        ad_group_ad_service = self._client.GetService('AdGroupAdService', version=self._version)
        
        #construct operations
        operations = []
        for i, j in zip(data['Ad group ID'], non_eta['Ad ID']):
            operations.append({'operator': 'REMOVE', 
                               'operand': {'xsi_type': 'AdGroupAd',
                                           'adGroupId': i,
                                           'ad': {'id': j}
                                          }
                               })

        for i in xrange(0, len(operations), self._max_operations):
            tmp_operations = operations[i:i+self._max_operations]
            result = ad_group_ad_service.mutate(tmp_operations)
            print tmp_operations
            if self._verbose:
                for ad in result['value']:
                    print ('Ad with id "{0}" and type "{1}" was deleted.'.format(ad['ad']['id'], ad['ad']['Ad.Type']))
    
    
    def low_impression_share(self, account_id, campaign_id):
        data = self.get_ad_data(account_id, campaign_id)
        count_ads = data.groupby(['Campaign ID', 'Ad group ID'])['Ad ID'].count().reset_index()
        sum_impressions = data.groupby(['Campaign ID', 'Ad group ID'])['Impressions'].sum().reset_index()   
        sum_impressions.columns = ['Campaign ID', 'Ad group ID', 'Total Impressions']
        #adgroup with greater than _max_ads
        filtered = count_ads[count_ads['Ad ID']>self._max_ads][['Campaign ID', 'Ad group ID']]
        #add info 
        with_info = pd.merge(filtered, data, how='left', on=['Campaign ID', 'Ad group ID'])
        with_info = pd.merge(with_info, sum_impressions, how='left', on=['Campaign ID', 'Ad group ID'])
        with_info = with_info[['Ad group ID', 'Ad ID', 'Impressions', 'Clicks', 'Total Impressions']]
        #ctr & impression share
        with_info['ctr'] = with_info['Clicks']/with_info['Impressions']
        with_info['imp_share'] = with_info['Impressions']/with_info['Total Impressions']
        with_info = with_info.fillna(0)
        #rank
        share_rank = with_info.groupby(['Ad group ID'])['imp_share'].rank(ascending=False).to_frame()
        share_rank.columns = ['share_rank']
        #merged
        merged = pd.merge(with_info, share_rank, left_index=True, right_index=True)
        merged = merged.sort_values(['Ad group ID', 'share_rank'])
        return merged


    def ads_to_pause_low_ctr_high_std_dev(self, account_id, campaign_id):
        data = self.get_ad_data(account_id, campaign_id)
        count_ads = data.groupby(['Campaign ID', 'Ad group ID'])['Ad ID'].count().reset_index()
        #adgroup with greater than _max_ads
        filtered = count_ads[count_ads['Ad ID']>self._max_ads][['Campaign ID', 'Ad group ID']]
        #add info 
        with_info = pd.merge(filtered, data, how='left', on=['Campaign ID', 'Ad group ID'])
        with_info = with_info[['Ad group ID', 'Ad ID', 'Impressions', 'Clicks']]
        #ctr
        with_info['ctr'] = with_info['Clicks']/with_info['Impressions']
        with_info = with_info.fillna(0)
        with_info['std'] = np.sqrt((with_info['ctr']*(1-with_info['ctr']))/with_info['Impressions'])
        with_info = with_info.fillna(0)
        with_info['ctr_adjusted'] = with_info['ctr'] - with_info['std']
        #rank
        ranking = with_info.groupby(['Ad group ID'])['ctr_adjusted'].rank(ascending=False).to_frame()
        ranking.columns = ['ranking']
        #merged
        merged = pd.merge(with_info, ranking, left_index=True, right_index=True)
        #rank >= max_ads
        #TODO: handle ties
        to_be_paused = merged[(merged.ranking>=self._max_ads)]
        return zip(list(to_be_paused['Ad group ID'].values),list(to_be_paused['Ad ID'].values))   

        
    def ads_to_pause(self, account_id, campaign_id):
        data = self.get_ad_data(account_id, campaign_id)
        count_ads = data.groupby(['Campaign ID', 'Ad group ID'])['Ad ID'].count().reset_index()
        #adgroup with greater than _max_ads
        filtered = count_ads[count_ads['Ad ID']>self._max_ads][['Campaign ID', 'Ad group ID']]
        #add info 
        with_info = pd.merge(filtered, data, how='left', on=['Campaign ID', 'Ad group ID'])
        with_info = with_info[['Ad group ID', 'Ad ID', 'Impressions', 'Clicks']]
        #ctr
        with_info['ctr'] = with_info['Clicks']/with_info['Impressions']
        with_info = with_info.fillna(0)
        #rank
        ranking = with_info.groupby(['Ad group ID'])['ctr'].rank(ascending=False).to_frame()
        ranking.columns = ['ranking']
        #merged
        merged = pd.merge(with_info, ranking, left_index=True, right_index=True)
        #rank >= max_ads & impressions > 100
        to_be_paused = merged[(merged.ranking>=self._max_ads)&(merged.Impressions>100)]
        return zip(list(to_be_paused['Ad group ID'].values),list(to_be_paused['Ad ID'].values))
    

    def pause_ads(self, account_id, ad_group_id, ad_id, verbose=True):
        self._client.SetClientCustomerId(account_id)
        ad_group_ad_service = self._client.GetService('AdGroupAdService', version=self._version)
    
        operations = [{
            'operator': 'SET',
            'operand': {
                'adGroupId': ad_group_id,
                'ad': {'id': ad_id},
                'status': 'PAUSED'
            }
        }]
        ads = ad_group_ad_service.mutate(operations)
        
        if verbose:
            # Display results.
            for ad in ads['value']:
                print 'Ad with id \'%s\' was updated.'% ad['ad']['id']    
    
    def run(self):
        accounts = self.get_accounts()
        for account in accounts:
            campaigns = self.get_campaigns(account)
            for campaign in campaigns:
                pause_these = self.ads_to_pause(account, campaign)
                if pause_these:
                    for k in pause_these:
                        ad_group, ad = k
                        self.pause_ads(account, ad_group, ad)
                        
    def pause_low_ctr_high_std_dev(self):
        accounts = self.get_accounts()
        for account in accounts:
            campaigns = self.get_campaigns(account)
            for campaign in campaigns:
                pause_these = self.ads_to_pause_low_ctr_high_std_dev(account, campaign)
                print pause_these
                if pause_these:
                    for k in pause_these:
                        ad_group, ad = k
                        try:
                            self.pause_ads(account, ad_group, ad)
                        except:
                            pass

In [249]:
a = google_adwords('us', '20170901', '20170912')

In [144]:
a.get_accounts(True)

[('9658766582', 'us_jobseeker_usd_exactmatch_0_en'),
 ('4103148574', 'us_jobseeker_usd_exactmatch_3_en'),
 ('8708501136', 'us_jobseeker_usd_exactmatch_5_en'),
 ('8495299372', 'us_jobseeker_usd_exactmatch_2_en'),
 ('8745534751', 'us_jobseeker_usd_exactmatch_1_en'),
 ('4403620381', 'us_jobseeker_usd_broadmatch_0_en'),
 ('9769164738', 'us_jobseeker_usd_exactmatch_4_en'),
 ('5902912087', 'us_jobseeker_usd_exactmatch_7_active'),
 ('1859451522', 'us_jobseeker_usd_broadmatch_2_en'),
 ('1912824586', 'us_jobseeker_usd_exactmatch_6_en'),
 ('4154173554', 'us_jobseeker_usd_broadmatch_1_en')]

In [246]:
a.get_campaigns_via_report(8495299372, True)

[(181368953, 'job_campaign_20150924_1_(exact)_(en)'),
 (180911153, 'company_campaign_20150908_1_(exact)_(en)'),
 (180911273, 'job_campaign_20150909_1_(exact)_(en)'),
 (181368833, 'geo_campaign_20150923_1_(exact)_(en)'),
 (181369073, 'company_campaign_20150924_1_(exact)_(en)')]

In [255]:
non_eta = a.get_not_eta_ad_data_via_report(8495299372, 181368833)

non-eta %: 0.977478947712


In [256]:
len(non_eta)

44922

In [241]:
non_eta[non_eta['Ad type']!='Text ad']

Campaign ID  Ad group ID Ad group state         Ad ID  \
48364    180911273   8719217273        enabled  163745044495   
48366    180911273   8719170233        enabled  163745044921   
48367    180911273   8719170233        enabled  163745044933   
48368    180911273   8719170233        enabled  163745044939   
48369    180911273   8719123193        enabled  163745045203   
48371    180911273   8718750473        enabled  163745045404   
48373    180911273   8719140713        enabled  163745045884   
48374    180911273   8719159673        enabled  163745045920   
48375    180911273   8719159673        enabled  163745045923   
48376    180911273   8719159673        enabled  163745045935   
48377    180911273   8719168553        enabled  163745045965   
48378    180911273   8719596953        enabled  163745046160   
48380    180911273   8718912353        enabled  163745046370   
48363    180911273   8719701593        enabled  163745044306   
48381    180911273   8718818513        enabled  163745046418   
44404    180911273   8718893513        enabled  163745617156   
44405    180911273   8719624913        enabled  163745617174   
44407    180911273   8719452473        enabled  163745617336   
44408    180911273   8719130513        enabled  163745617351   
44409    180911273   8719130513        enabled  163745617357   
44410    180911273   8719149473        enabled  163745617390   
44411    180911273   8719149473        enabled  163745617393   
44412    180911273   8719158353        enabled  163745617408   
44413    180911273   8719689473        enabled  163745617423   
44414    180911273   8719689473        enabled  163745617432   
44415    180911273   8719586753        enabled  163745617600   
44416    180911273   8719083473        enabled  163745617612   
44417    180911273   8719414313        enabled  163745617621   
44403    180911273   8718874553        enabled  163745617105   
44418    180911273   8719414313        enabled  163745617630   
...            ...          ...            ...           ...   
30027    180911273   8718903353        enabled  204277380195   
17388    180911273   8723255393        enabled  204277379475   
21681    180911273   8719403393        enabled  204277348050   
2085     180911273   8719224953        enabled  163745345956   
21651    180911273   8719157873        enabled  163752205190   
17331    180911273   8719302353        enabled  204277348269   
17355    180911273   8723261153        enabled  204277349259   
18841    180911273   8719181993        enabled  163750877450   
15199    180911273   8718739433        enabled  163750562855   
1985     180911273   8719451513        enabled  163745226607   
27602    180911273   8723268713        enabled  163751406200   
60141    180911273   8719776593        enabled  204277349694   
22925    180911273   8718739433        enabled  163750562867   
17458    180911273   8719590593        enabled  163752295592   
7070     180911273   8719555193        enabled  163746413026   
13540    180911273   8723248553        enabled  163747797522   
15360    180911273   8719340873        enabled  163750663646   
57948    180911273   8719555193        enabled  163746413011   
22388    180911273   8718754913        enabled  204277379751   
57450    180911273   8723268713        enabled  163751406188   
11094    180911273   8719035593        enabled  163746811086   
3000     180911273   8719534673        enabled  163746049861   
30041    180911273   8719684193        enabled  204277380696   
21951    180911273   8718901553        enabled  163751507927   
3489     180911273   8719508513        enabled  163745491189   
241      180911273   8719015913        enabled  163745349079   
28051    180911273   8719423793        enabled  204277379439   
22473    180911273   8719624673        enabled  198070325442   
19293    180911273   8718901553        enabled  163751507939   
21806    180911273   8719722833        enabled  163752294383   

                Ad type  Impressions  

In [218]:
a.delete_multiple_ads(4103148574, non_eta)

[{'operator': 'REMOVE', 'operand': {'adGroupId': 22265540713, 'ad': {'id': 98218883233}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265872393, 'ad': {'id': 98237167273}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265872273, 'ad': {'id': 98237167033}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265871913, 'ad': {'id': 98237135473}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265870233, 'ad': {'id': 98236997113}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265869633, 'ad': {'id': 98236981153}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265881033, 'ad': {'id': 98250858553}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265880673, 'ad': {'id': 98250833713}, 'xsi_type': 'AdGroupAd'}}, {'operator': 'REMOVE', 'operand': {'adGroupId': 22265879473, 'ad': {'id': 98237

In [220]:
non_eta

Campaign ID  Ad group ID Ad group state        Ad ID  Ad type  \
0        341883433  22265540713        enabled  98218883233  Text ad   
52863    341883433  22265872393        enabled  98237167273  Text ad   
52862    341883433  22265872273        enabled  98237167033  Text ad   
52861    341883433  22265871913        enabled  98237135473  Text ad   
52860    341883433  22265870233        enabled  98236997113  Text ad   
52859    341883433  22265869633        enabled  98236981153  Text ad   
52858    341883433  22265881033        enabled  98250858553  Text ad   
52857    341883433  22265880673        enabled  98250833713  Text ad   
52856    341883433  22265879473        enabled  98237351593  Text ad   
52855    341883433  22265877433        enabled  98237317393  Text ad   
52854    341883433  22265876713        enabled  98237298193  Text ad   
52853    341883433  22265875033        enabled  98237241073  Text ad   
52852    341883433  22265650273        enabled  98222900473  Text ad   
52851    341883433  22265149273        enabled  98211438673  Text ad   
52850    341883433  22265145553        enabled  98211068833  Text ad   
52849    341883433  22265868313        enabled  98236917673  Text ad   
52864    341883433  22265872633        enabled  98237169073  Text ad   
52848    341883433  22265866513        enabled  98236850353  Text ad   
52865    341883433  22265587393        enabled  98219966953  Text ad   
52867    341883433  22265588233        enabled  98219995753  Text ad   
52883    341883433  22265913673        enabled  98251144873  Text ad   
52882    341883433  22265131633        enabled  98210359633  Text ad   
52881    341883433  22265592553        enabled  98220162073  Text ad   
52880    341883433  22265150713        enabled  98211448633  Text ad   
52879    341883433  22265592073        enabled  98220158353  Text ad   
52878    341883433  22265591713        enabled  98220148513  Text ad   
52877    341883433  22265591233        enabled  98220143713  Text ad   
52876    341883433  22265591113        enabled  98220142873  Text ad   
52875    341883433  22265144953        enabled  98210953153  Text ad   
52874    341883433  22265143153        enabled  98210833873  Text ad   
...            ...          ...            ...          ...      ...   
28566    341883433  22264927633        enabled  98206620193  Text ad   
8833     341883433  22265329873        enabled  98215176313  Text ad   
35039    341883433  22264927633        enabled  98206620433  Text ad   
35462    341883433  22264069753        enabled  98149375753  Text ad   
75567    341883433  22265827513        enabled  98236237393  Text ad   
74721    341883433  22264434793        enabled  98182779793  Text ad   
32566    341883433  22266312913        enabled  98263421113  Text ad   
16992    341883433  22265067553        enabled  98209091113  Text ad   
45078    341883433  22265956873        enabled  98251261993  Text ad   
54       341883433  22265512513        enabled  98218581913  Text ad   
25038    341883433  22265433313        enabled  98217409513  Text ad   
21727    341883433  22264539313        enabled  98195097673  Text ad   
26941    341883433  22265496433        enabled  98218365673  Text ad   
36517    341883433  22266277873        enabled  98263092913  Text ad   
61556    341883433  22266166633        enabled  98254370353  Text ad   
38939    341883433  22264645633        enabled  98202506233  Text ad   
71999    341883433  22264760113        enabled  98205456073  Text ad   
75557    341883433  22264665913        enabled  98204247073  Text ad   
59828    341883433  22266282193        enabled  98263116913  Text ad   
49270    341883433  22265169793        enabled  98212138873  Text ad   
29854    341883433  22264539313        enabled  98195097553  Text ad   
43195    341883433  22265512513        enabled  98218581193  Text ad   
19804    341883433  22264163233        enabled  98152888873  Text ad   
24863    341883433  22265398273        enabled 